# Des Artikels erster Teil

In [ ]:
import json
path = "export.json"
with open(path, encoding = "utf-8") as f:
  data = json.loads(f.read())

In [ ]:
# JSON-Hierarchie in flache Datenstruktur umwandeln
table = ({**ord, **subOrd, **item}
  for ord in data['orders']['orders']
  for subOrd in ord['subOrders']
  for item in subOrd['lineItems'])

In [ ]:
# Daten in einen DataFrame importieren
import pandas
df = pandas.DataFrame(table)

# Spalte mit interpretiertem Zeitstempel ergänzen
df['date'] = pandas.to_datetime(
  df['creationDate']
)

In [ ]:
# Behalte nur die genannten Spalten (in der genannten Reihenfolge)
df = df[['date', 'orderId',
  'orderValue', 'title', 'price',
  'quantity', 'totalPrice']]

In [ ]:
# Unnütze Einträge aussortieren
dummies = ["Enthaltene Pfandbeträge",
  "Getränke-Sperrgutaufschlag",
  "TimeSlot"]
df = df[~df['title'].isin(dummies)]

In [ ]:
# Datumsspalte zum Index erklären
df = df.set_index(['date'])

In [ ]:
df

In [ ]:
# Monatliche Einkaufssummen plotten
# Die folgenden Zeilen auskommentieren, um die Auflösung der Grafik anzupassen

#import matplotlib.pyplot as plt
#plt.rcParams['figure.dpi'] = 300
#plt.rcParams['savefig.dpi'] = 300

df.resample('m').sum()['totalPrice'].plot(kind='bar')

In [ ]:
# Nach Produkttiteln gruppieren
df_title = df.groupby('title') 

# Minimum und Maximum jedes Produktes auswählen
min = df_title.min()['price']
max = df_title.max()['price']

# Fluktuation berechnen, sortieren und ausgeben
fluc = (max - min) / (max + min)
fluc.sort_values(ascending=False).to_frame('Fluctuation')

In [ ]:
# Unit-Klasse importieren und damit experimentieren
from viktualien.util.units import Unit, UnitType

p = Unit.parse("Pils 24x0,33l")
w1 = Unit.parse("Hefeweizen 5L Fass")
w2 = Unit.parse("Weißbier 6x0,5l")
p > w1 + w2 # Ergibt False

In [ ]:
# Produktgruppen nach Anzahl summieren
df_sum = df_title.sum()[['quantity']]

# Eine Spalte mit verarbeiteten Einheiten ergänzen
df_sum['unit'] = df_sum.index.map(Unit.parse)

# Produkte aussortieren, bei denen keine Einheit geparst werden konnte
df_sum = df_sum[df_sum['unit'].notna()]

# Eine Spalte mit der Gesamtmenge (Einheit mal Anzahl) ergänzen
df_sum['total'] = df_sum['unit'] * df_sum['quantity']
df_sum

In [ ]:
# Filtere nach Produkten mit Gewichtsangaben
df_weight = df_sum[df_sum['unit'].map(
  lambda unit: unit.unit_type == UnitType.WEIGHT
)]
# Sortiere die gefilterte Liste absteigend nach der Gesamtmenge
df_weight.sort_values('total', ascending = False)

In [ ]:
# Das gleiche nochmal mit Produkten mit Volumenangaben
df_volume = df_sum[df_sum['unit'].map(
  lambda unit: unit.unit_type == UnitType.VOLUME
)]
df_volume.sort_values('total', ascending = False)

# Des Artikels zweiter Teil

In [ ]:
# Order-IDs aus der Bestelliste extrahieren
order_ids = list(set(df['orderId']))

In [ ]:
# Per HTTPX alle Bestelldetails über die API abrufen.
import httpx
from tqdm import tqdm # tqdm sorgt für einen Fortschrittsbalken

rstp = "ey...9g" # Hier den RSTP-Cookie aus dem Browser einsetzen
cookies = {"rstp": rstp}

def fetch_order(id):
    url = f"https://shop.rewe.de/api/orders/{id}?constraint=rewe"
    return httpx.get(url, cookies = cookies).json()

detailed_orders = [fetch_order(id) for id in tqdm(order_ids)]

In [ ]:
# Konfiguration aufsetzen, dies muss nur einmalig gemacht werden.
# Dabei wird u.a. ein Cache-Verzeichnis für Produkt-Details angelegt.
from viktualien.config import Config
Config.set(Config())

In [ ]:
from viktualien.rewe import api as rewe_api
from viktualien.rewe import model as rewe_model

# Kategorien-Baum abfragen
categories = rewe_api.load_categories()

# Bestelldetails importieren
orders = rewe_model.Orders(
    [rewe_api.parse_order(order, categories) for order in detailed_orders]
)

In [ ]:
# Die API mit den EAN-Daten abfragen und dadurch die Kategorien verfeinern.
orders2 = rewe_api.narrow_categories_in(categories, orders)

In [ ]:
# Ausgabe des Baumdiagramms
from viktualien.rewe import charts
from viktualien.rewe import stats

charts.treechart(stats.categories_metric(
  orders2.all_line_items.aggregate_add(lambda item: item.total_price),
  orders2.all_product_infos,
  categories, max_depth = 2
))